In [375]:
import pandas as pd
import geopandas as gpd


## 서울특별시 전월세 가져오기

In [376]:
df_23 = pd.read_csv('서울특별시_전월세가_2023.csv', encoding='utf-8')
df_23.head()

접수년도  자치구코드 자치구명  법정동코드   법정동명  지번구분코드 지번구분   본번   부번    층  ...  보증금(만원)  \
0  2023  11440  마포구  11000   노고산동     1.0   대지  1.0  1.0  8.0  ...    10000   
1  2023  11440  마포구  11000   노고산동     1.0   대지  1.0  1.0  5.0  ...    10000   
2  2023  11440  마포구  11000   노고산동     1.0   대지  1.0  1.0  9.0  ...    21000   
3  2023  11170  용산구  11300  원효로2가     1.0   대지  1.0  0.0  9.0  ...    23900   
4  2023  11440  마포구  11000   노고산동     1.0   대지  1.0  1.0  9.0  ...    22000   

  임대료(만원)        건물명    건축년도  건물용도         계약기간  신규계약구분 갱신청구권사용    종전보증금 종전임대료  
0      40  \t(1-1)\t  1998.0  오피스텔  23.01~24.01      신규     NaN      0.0   0.0  
1      55  \t(1-1)\t  1998.0  오피스텔  23.02~24.02      갱신     NaN  10000.0  55.0  
2       0  \t(1-1)\t  1998.0  오피스텔  23.02~24.02      신규     NaN      0.0   NaN  
3       0    \t(1)\t  1990.0  오피스텔  23.09~25.09      신규     NaN      0.0   NaN  
4       0  \t(1-1)\t  1998.0  오피스텔          NaN     NaN     NaN      NaN   NaN  

[5 rows x 23 columns]

In [377]:
len(df_23['자치구명'].unique())

25

In [378]:
df_23['자치구명'].value_counts(ascending=False).head(10)

송파구     46398
강남구     36943
강서구     36397
관악구     30862
강동구     30636
마포구     28013
서초구     27365
영등포구    25995
동작구     24368
광진구     23416
Name: 자치구명, dtype: int64

In [379]:
df_23['법정동명'].value_counts(ascending=False)

봉천동    15757
신림동    13886
화곡동    12016
상계동     9642
신정동     8379
       ...  
산림동        1
재동         1
궁정동        1
관훈동        1
북창동        1
Name: 법정동명, Length: 402, dtype: int64

In [380]:
df_bong = df_23[df_23['자치구명'] == '관악구']
df_bong['건물용도'].value_counts(ascending=False)

단독다가구    17944
아파트       5889
연립다세대     4708
오피스텔      2321
Name: 건물용도, dtype: int64

In [381]:
df_bong = df_23[df_23['자치구명'] == '송파구']
df_bong['건물용도'].value_counts(ascending=False)

아파트      20968
연립다세대    15200
오피스텔      5602
단독다가구     4628
Name: 건물용도, dtype: int64

## 아파트 월세 제외

In [382]:
df = df_23[['법정동명', '전월세구분', '임대료(만원)', '건물용도']]
df = df[df['건물용도'] != '아파트']
df = df[df['전월세구분'] == '월세']
df

법정동명 전월세구분  임대료(만원)   건물용도
0       노고산동    월세       40   오피스텔
1       노고산동    월세       55   오피스텔
5        방배동    월세       55   오피스텔
6        사당동    월세       22   오피스텔
7       노고산동    월세       30   오피스텔
...      ...   ...      ...    ...
545801   삼청동    월세       50  단독다가구
545802   대조동    월세       85  단독다가구
545807   자곡동    월세       50  단독다가구
545808   상도동    월세      100  단독다가구
545809   대치동    월세      150  단독다가구

[188799 rows x 4 columns]

In [383]:
df['법정동명'].value_counts(ascending=False)

봉천동     8549
신림동     8475
화곡동     4798
사당동     3307
마곡동     3097
        ... 
팔판동        1
압구정동       1
궁정동        1
주교동        1
홍파동        1
Name: 법정동명, Length: 386, dtype: int64

In [384]:
df_avg = df.groupby('법정동명')['임대료(만원)'].mean().sort_values(ascending=False)
df_avg

법정동명
한남동      182.172691
신천동      173.900000
신문로2가    151.714286
압구정동     150.000000
의주로1가    149.461538
            ...    
양평동1가     36.435294
토정동       35.000000
하중동       32.000000
을지로6가     27.666667
문래동1가     21.545455
Name: 임대료(만원), Length: 386, dtype: float64

## 법정동 경계 데이터

In [385]:
# 법정동 shp -> pd
df_geo = gpd.read_file('emd.shp', encoding='CP949')
df_geo = df_geo[df_geo['EMD_CD'].str.startswith('11')]
df_geo = df_geo.rename(columns={'EMD_KOR_NM': '법정동명'})
df_geo

EMD_CD       EMD_ENG_NM 법정동명  \
0    11110101    Cheongun-dong  청운동   
1    11110102      Singyo-dong  신교동   
2    11110103   Gungjeong-dong  궁정동   
3    11110104       Hyoja-dong  효자동   
4    11110105  Changseong-dong  창성동   
..        ...              ...  ...   
462  11740106     Dunchon-dong  둔촌동   
463  11740107        Amsa-dong  암사동   
464  11740108    Seongnae-dong  성내동   
465  11740109     Cheonho-dong  천호동   
466  11740110      Gangil-dong  강일동   

                                              geometry  
0    POLYGON ((953700.022 1954605.065, 953693.871 1...  
1    POLYGON ((953233.465 1953996.984, 953235.183 1...  
2    POLYGON ((953560.228 1954257.466, 953561.190 1...  
3    POLYGON ((953519.843 1953890.785, 953518.489 1...  
4    POLYGON ((953516.123 1953734.362, 953516.526 1...  
..                                                 ...  
462  POLYGON ((969669.593 1948748.489, 969656.716 1...  
463  POLYGON ((968514.203 1950677.234, 968505.336 1...  
464  POLYGON ((967686.073 1948534.011, 967685.029 1...  
465  POLYGON ((968336.280 1950222.697, 968337.437 1...  
466  POLYGON ((970882.440 1951500.730, 970882.447 1...  

[467 rows x 4 columns]

In [386]:
df_mg = pd.merge(df_geo, df_avg, on='법정동명', how='outer')
df_mg = df_mg[['법정동명', '임대료(만원)', 'geometry']]
df_mg.sample(10)

법정동명    임대료(만원)                                           geometry
299    증산동  44.147287  POLYGON ((947977.081 1954592.795, 947978.882 1...
319   북가좌동  48.561208  POLYGON ((948287.035 1953042.391, 948285.978 1...
213    용답동  58.766097  POLYGON ((959605.554 1952689.835, 959662.543 1...
282     창동  52.575975  POLYGON ((960450.130 1962444.879, 960437.777 1...
301  충정로2가  53.107692  POLYGON ((952914.122 1951891.753, 952909.900 1...
39     삼청동  94.842105  POLYGON ((953807.418 1955517.066, 953811.095 1...
69    명륜1가  61.485356  POLYGON ((955688.361 1954895.338, 955688.921 1...
120  인현동2가        NaN  POLYGON ((955646.926 1951928.688, 955646.658 1...
254  동선동3가  52.830508  POLYGON ((957590.128 1954793.502, 957590.144 1...
388  당산동3가  57.305085  POLYGON ((947137.589 1947278.207, 947136.308 1...

In [387]:
# 좌표변환
import pyproj
from shapely.ops import transform

epsg5179 = pyproj.Proj(init='epsg:5179')
epsg4326 = pyproj.Proj(init='epsg:4326')

def epsg5179_to_epsg4326(geometry):
    return transform(lambda x, y: pyproj.transform(epsg5179, epsg4326, x, y), geometry)

df_mg['geometry'] = df_mg['geometry'].apply(epsg5179_to_epsg4326)
df_mg

c:\Users\rnlay\AppData\Local\Programs\Python\Python311\Lib\site-packages\pyproj\crs\crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
c:\Users\rnlay\AppData\Local\Programs\Python\Python311\Lib\site-packages\pyproj\crs\crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
C:\Users\rnlay\AppData\Local\Temp\ipykernel_29960\3715204241.py:9: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotc

법정동명     임대료(만원)                                           geometry
0    청운동  147.823529  POLYGON ((126.97556 37.58968, 126.97549 37.589...
1    신교동   60.342105  POLYGON ((126.97031 37.58418, 126.97033 37.584...
2    궁정동   47.000000  POLYGON ((126.97400 37.58654, 126.97401 37.586...
3    효자동   85.500000  POLYGON ((126.97356 37.58323, 126.97355 37.582...
4    창성동   62.200000  POLYGON ((126.97353 37.58182, 126.97354 37.581...
..   ...         ...                                                ...
462  둔촌동   48.271144  POLYGON ((127.15669 37.53756, 127.15654 37.537...
463  암사동   45.594828  POLYGON ((127.14353 37.55490, 127.14343 37.554...
464  성내동   47.324013  POLYGON ((127.13424 37.53556, 127.13423 37.535...
465  천호동   51.026956  POLYGON ((127.14153 37.55080, 127.14154 37.550...
466  강일동   49.440860  POLYGON ((127.17030 37.56240, 127.17030 37.562...

[467 rows x 3 columns]

In [388]:
# NaN 값은 0으로 하고, 정수화
df_mg['임대료(만원)'] = df_mg['임대료(만원)'].round(1)
df_mg['임대료(만원)'] = df_mg['임대료(만원)'].fillna(0).astype(int)
df_mg['임대료(만원)'] = df_mg['임대료(만원)'].astype(int)
df_mg

법정동명  임대료(만원)                                           geometry
0    청운동      147  POLYGON ((126.97556 37.58968, 126.97549 37.589...
1    신교동       60  POLYGON ((126.97031 37.58418, 126.97033 37.584...
2    궁정동       47  POLYGON ((126.97400 37.58654, 126.97401 37.586...
3    효자동       85  POLYGON ((126.97356 37.58323, 126.97355 37.582...
4    창성동       62  POLYGON ((126.97353 37.58182, 126.97354 37.581...
..   ...      ...                                                ...
462  둔촌동       48  POLYGON ((127.15669 37.53756, 127.15654 37.537...
463  암사동       45  POLYGON ((127.14353 37.55490, 127.14343 37.554...
464  성내동       47  POLYGON ((127.13424 37.53556, 127.13423 37.535...
465  천호동       51  POLYGON ((127.14153 37.55080, 127.14154 37.550...
466  강일동       49  POLYGON ((127.17030 37.56240, 127.17030 37.562...

[467 rows x 3 columns]

## folium 시각화

In [389]:
import folium
import branca

In [392]:
m = folium.Map(location=[37.5665, 126.9780], zoom_start=12)  # 서울을 중심으로 맵 생성
df_mg.crs = "EPSG:4326" # ValueError: Cannot transform naive geometries. Please set a crs on the object first. 오류 발생 시

# Define a linear colormap
colormap = branca.colormap.LinearColormap(
    vmin=df_mg["임대료(만원)"].quantile(0.0),
    vmax=df_mg["임대료(만원)"].quantile(1),
    colors=["white","red"],
    caption="임대료(만원)",
)

# Define a tooltip
tooltip = folium.GeoJsonTooltip(
    fields=["법정동명", "임대료(만원)"],
    aliases=["법정동명:", "임대료(만원):"],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 1px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """,
    max_width=800,
)

# Create a GeoJson layer
g = folium.GeoJson(
    df_mg,
    style_function=lambda x: {
        "fillColor": colormap(x["properties"]["임대료(만원)"])
        if x["properties"]["임대료(만원)"] is not None
        else "transparent",
        "color": "black",
        "weight": 1, # 경계 두께
        "fillOpacity": 0.6,
    },
    tooltip=tooltip,
).add_to(m)

# Add the colormap to the map
colormap.add_to(m)

m